In [1]:
import pandas as pd
import numpy as np

### mapping of ingredients to its base ingredient 

In [2]:
import pickle

# Load the dictionary from the file
with open('mapping_dict.pkl', 'rb') as f:
    mapping_dict = pickle.load(f)

mapping_dict


{'lime': 'lime',
 'pickled ginger': 'pickled ginger',
 'pickled ginger juice': 'pickled ginger juice',
 'pickled jalapeño': 'pickled jalapeño',
 'pickle brine': 'pickle brine',
 'pickle juice': 'pickle juice',
 'jalapeño': 'jalapeño',
 'jalapeńo': 'jalapeño',
 'jalapeno': 'jalapeño',
 'jalopeno': 'jalapeño',
 'ginger': 'ginger',
 'garlic': 'garlic',
 'peppers': 'bell pepper',
 'bell pepper': 'bell pepper',
 'honey': 'honey',
 'chili flake': 'chili flake',
 'cucumber': 'cucumber',
 'basil': 'basil',
 'avocado': 'avocado',
 'avocdos': 'avocado',
 'peanut': 'peanut',
 'vinegar': 'vinegar',
 'thyme': 'thyme',
 'arugula': 'arugula',
 'tacos': 'taco shells',
 'lettuce': 'lettuce',
 'Greek yogurt': 'yogurt',
 'mayo': 'mayo',
 'buttermilk': 'buttermilk',
 'parsley': 'parsley',
 'dill': 'dill',
 'garlic powder': 'garlic powder',
 'onion powder': 'onion powder',
 'tortilla': 'tortilla',
 'apple cider vinegar': 'apple cider vinegar',
 'apple cider': 'apple cider vinegar',
 'balsamic': 'vinegar',


In [3]:
df = pd.read_csv('final_recipes.csv')

In [4]:
df.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 2350 entries, 0 to 2349
Data columns (total 11 columns):
 #   Column                        Non-Null Count  Dtype 
---  ------                        --------------  ----- 
 0   title                         2350 non-null   object
 1   prep_time                     2350 non-null   object
 2   cook_time                     2350 non-null   object
 3   total_time                    2350 non-null   object
 4   ingredients                   2350 non-null   object
 5   ingredients with measurement  2350 non-null   object
 6   instructions                  2350 non-null   object
 7   calories                      2350 non-null   object
 8   servings                      2350 non-null   int64 
 9   images                        2350 non-null   object
 10  type_of_meal                  2350 non-null   object
dtypes: int64(1), object(10)
memory usage: 202.1+ KB


In [5]:
# df = df.loc[0:1500]


In [6]:
import ast
def safe_literal_eval(val):
    if val is None:
        return val
    try:
        return ast.literal_eval(val)
    except (ValueError, SyntaxError):
        return val
    
# Convert string representations of lists to actual lists
df['ingredients'] = df['ingredients'].apply(safe_literal_eval)


## Function mapping ingredients to base ingredient

In [7]:
def extract_base_ingr(ingredients_list, instructions):
    base_ingr = []
    for ingr in ingredients_list:
        if ingr is None:  # Check if ingr is None
            continue
        ingr = ingr.lower()
        found = False
        for key in mapping_dict:
            if found:
                break
            if key.lower() in ingr:
                found = True
                base_ingr.append(mapping_dict[key].lower())
              
    # Remove duplicates
    seen = set()
    base_ingr = [x for x in base_ingr if not (x in seen or seen.add(x))]
    return base_ingr
    
df['base_ingredients'] = df.apply(lambda row: extract_base_ingr(row['ingredients'], row['instructions']), axis=1)


## Function mapping ingredients to base ingredient in INSTRUCTIONS

In [8]:
def base_instructions(instructions,ingredients_list):
    print(instructions)
    for ingr in ingredients_list:
        ingr = ingr.lower()
        found = False
        for key in mapping_dict:
            if found == True:
                break
            if key.lower() in ingr:
                found = True
                instructions = instructions.replace(key.lower(),mapping_dict[key].lower())
    print(instructions)
    return instructions

df['instructions']  = df.apply(lambda row: base_instructions(row['instructions'], row['ingredients']), axis=1)


['1. To make the dressing. Combine all ingredients in a jar. Season to taste with chili flakes.', '2. In a bowl, toss the steak with tamari and 2-3 tablespoons of the dressing, rubbing the dressing onto the steak.', '3. Set your grill, grill pan, or skillet to medium-high heat. Grill the steak until lightly charred, 5-8 minutes for medium-rare, per side. Remove the steaks and allow them to rest for 5-10 minutes. Slice the steak.', '4. Meanwhile, in a bowl, toss the cucumbers with pickled ginger and 3 tablespoons dressing. In a separate bowl, toss the mango with herbs, lime juice, and chili flakes.', '5. Spoon the reserved dressing over the slices of steak, then serve the steak over bowls of rice. Top with cucumber, mango, avocado, and peanuts. Enjoy!']
['1. To make the dressing. Combine all ingredients in a jar. Season to taste with chili flakes.', '2. In a bowl, toss the steak with tamari and 2-3 tablespoons of the dressing, rubbing the dressing onto the steak.', '3. Set your grill, g

IOPub data rate exceeded.
The notebook server will temporarily stop sending output
to the client in order to avoid crashing it.
To change this limit, set the config variable
`--NotebookApp.iopub_data_rate_limit`.

Current values:
NotebookApp.iopub_data_rate_limit=1000000.0 (bytes/sec)
NotebookApp.rate_limit_window=3.0 (secs)



In [9]:
df

title          prep_time  \
0        25 Minute Ginger Steak Mango Cucumber Bowls  {'minutes': '15'}   
1                         The Italian Salad Sandwich  {'minutes': '25'}   
2                Grilled Buffalo Ranch Chicken Tacos  {'minutes': '20'}   
3     Chicken Quesadillas with Creamy Chipotle Sauce  {'minutes': '20'}   
4      Sesame Ginger Steak Skewers with Peanut Sauce  {'minutes': '15'}   
...                                              ...                ...   
2345                         Fig Bourbon Cider Smash   {'minutes': '5'}   
2346                        Salted Watermelon Paloma  {'minutes': '10'}   
2347                      Blackberry Thyme Margarita   {'minutes': '5'}   
2348                    Sweet Bourbon Peach Lemonade   {'minutes': '5'}   
2349                    Hibiscus Cherry Vodka Spritz  {'minutes': '15'}   

              cook_time         total_time  \
0     {'minutes': '10'}  {'minutes': '25'}   
1      {'minutes': '5'}  {'minutes': '30'}   
2     {'minutes': '20'}  {'minutes': '40'}   
3     {'minutes': '10'}  {'minutes': '30'}   
4     {'minutes': '15'}  {'minutes': '30'}   
...                 ...                ...   
2345                  -   {'minutes': '5'}   
2346                  -  {'minutes': '10'}   
2347                  -   {'minutes': '5'}   
2348                  -   {'minutes': '5'}   
2349   {'minutes': '5'}  {'minutes': '20'}   

                                            ingredients  \
0     [lime juice, toasted sesame oil, fish sauce, f...   
1     [extra virgin olive oil, champagne vinegar, fi...   
2     [boneless chicken tenders or small thighs, sea...   
3     [canned chipotle chiles in adobo, extra virgin...   
4     [creamy peanut butter, tamari/soy sauce, Thai ...   
...                                                 ...   
2345  [apple cider, orange zest + 2 tablespoons juic...   
2346  [cubed watermelon, kosher salt, Florida’s Natu...   
2347  [fresh blackberries, small red plum, quartered...   
2348  [Florida's Natural® Brand Lemonade with Raspbe...   
2349  [fresh cherries, dried hibiscus flowers, honey...   

                           ingredients with measurement  \
0     {'lime juice': '2', 'toasted sesame oil': '3',...   
1     {'extra virgin olive oil': '1/2', 'champagne v...   
2     {'boneless chicken tenders or small thighs': '...   
3     {'canned chipotle chiles in adobo': '1/2', 'ex...   
4     {'creamy peanut butter': '1/2', 'tamari/soy sa...   
...                                                 ...   
2345  {'apple cider': '1/4', 'orange zest + 2 tables...   
2346  {'cubed watermelon': '2', 'kosher salt': 'seas...   
2347  {'fresh blackberries': '8', 'small red plum, q...   
2348  {"Florida's Natural® Brand Lemonade with Raspb...   
2349  {'fresh cherries': '3/4', 'dried hibiscus flow...   

                                           instructions  calories  servings  \
0     ['1. To make the dressing. Combine all ingredi...  472 kcal         6   
1     ['1. To make the dressing. Combine all ingredi...  699 kcal         6   
2     ['1. Set your grill, grill pan, or skillet to ...  582 kcal         6   
3     ["1. To make the dressing. Combine all ingredi...  672 kcal         4   
4     ['1. To make the peanut sauce. Add all ingredi...  419 kcal         6   
...                                                 ...       ...       ...   
2345  ['1. In a cocktail shaker, combine the apple c...   52 kcal         1   
2346  ['1. Add the watermelon to a blender and pulse...   68 kcal         1   
2347  ['1.\xa0Run a lime wedge around the rim of you...   84 kcal         1   
2348  ['1. In a blender, combine the lemonade and pe...  136 kcal         8   
2349  ['1. Add the cherries to a medium size pot. Us...  158 kcal         4   

                                                 images type_of_meal  \
0     https://www.halfbakedharvest.com/wp-content/up...  main-course   
1     https://www.halfbakedharvest.com/wp-content/up...  main-course   
2     http

In [10]:
# df.drop(columns=['images','servings','calories','prep_time','cook_time'],inplace=True)

In [11]:
df

title          prep_time  \
0        25 Minute Ginger Steak Mango Cucumber Bowls  {'minutes': '15'}   
1                         The Italian Salad Sandwich  {'minutes': '25'}   
2                Grilled Buffalo Ranch Chicken Tacos  {'minutes': '20'}   
3     Chicken Quesadillas with Creamy Chipotle Sauce  {'minutes': '20'}   
4      Sesame Ginger Steak Skewers with Peanut Sauce  {'minutes': '15'}   
...                                              ...                ...   
2345                         Fig Bourbon Cider Smash   {'minutes': '5'}   
2346                        Salted Watermelon Paloma  {'minutes': '10'}   
2347                      Blackberry Thyme Margarita   {'minutes': '5'}   
2348                    Sweet Bourbon Peach Lemonade   {'minutes': '5'}   
2349                    Hibiscus Cherry Vodka Spritz  {'minutes': '15'}   

              cook_time         total_time  \
0     {'minutes': '10'}  {'minutes': '25'}   
1      {'minutes': '5'}  {'minutes': '30'}   
2     {'minutes': '20'}  {'minutes': '40'}   
3     {'minutes': '10'}  {'minutes': '30'}   
4     {'minutes': '15'}  {'minutes': '30'}   
...                 ...                ...   
2345                  -   {'minutes': '5'}   
2346                  -  {'minutes': '10'}   
2347                  -   {'minutes': '5'}   
2348                  -   {'minutes': '5'}   
2349   {'minutes': '5'}  {'minutes': '20'}   

                                            ingredients  \
0     [lime juice, toasted sesame oil, fish sauce, f...   
1     [extra virgin olive oil, champagne vinegar, fi...   
2     [boneless chicken tenders or small thighs, sea...   
3     [canned chipotle chiles in adobo, extra virgin...   
4     [creamy peanut butter, tamari/soy sauce, Thai ...   
...                                                 ...   
2345  [apple cider, orange zest + 2 tablespoons juic...   
2346  [cubed watermelon, kosher salt, Florida’s Natu...   
2347  [fresh blackberries, small red plum, quartered...   
2348  [Florida's Natural® Brand Lemonade with Raspbe...   
2349  [fresh cherries, dried hibiscus flowers, honey...   

                           ingredients with measurement  \
0     {'lime juice': '2', 'toasted sesame oil': '3',...   
1     {'extra virgin olive oil': '1/2', 'champagne v...   
2     {'boneless chicken tenders or small thighs': '...   
3     {'canned chipotle chiles in adobo': '1/2', 'ex...   
4     {'creamy peanut butter': '1/2', 'tamari/soy sa...   
...                                                 ...   
2345  {'apple cider': '1/4', 'orange zest + 2 tables...   
2346  {'cubed watermelon': '2', 'kosher salt': 'seas...   
2347  {'fresh blackberries': '8', 'small red plum, q...   
2348  {"Florida's Natural® Brand Lemonade with Raspb...   
2349  {'fresh cherries': '3/4', 'dried hibiscus flow...   

                                           instructions  calories  servings  \
0     ['1. To make the dressing. Combine all ingredi...  472 kcal         6   
1     ['1. To make the dressing. Combine all ingredi...  699 kcal         6   
2     ['1. Set your grill, grill pan, or skillet to ...  582 kcal         6   
3     ["1. To make the dressing. Combine all ingredi...  672 kcal         4   
4     ['1. To make the peanut sauce. Add all ingredi...  419 kcal         6   
...                                                 ...       ...       ...   
2345  ['1. In a cocktail shaker, combine the apple c...   52 kcal         1   
2346  ['1. Add the watermelon to a blender and pulse...   68 kcal         1   
2347  ['1.\xa0Run a lime wedge around the rim of you...   84 kcal         1   
2348  ['1. In a blender, combine the lemonade and pe...  136 kcal         8   
2349  ['1. Add the cherries to a medium size pot. Us...  158 kcal         4   

                                                 images type_of_meal  \
0     https://www.halfbakedharvest.com/wp-content/up...  main-course   
1     https://www.halfbakedharvest.com/wp-content/up...  main-course   
2     http

### list of non-vegan ingredients in the database

In [12]:
with open('non_vegan_ingredients.txt', 'r') as file:
    non_vegan_ingr = [line.strip() for line in file]

non_vegan_ingr

['anchovy',
 'bbq sauce',
 'beer',
 'buffalo sauce',
 'butter',
 'buttermilk',
 'caramel',
 'cheese',
 'chocolate',
 'chocolate ice cream',
 'chocolate malt powder',
 'egg',
 'fish sauce',
 'gelatin',
 'heavy cream',
 'honey',
 'marsala wine',
 'marshmallow',
 'mayo',
 'meat - beef - beef',
 'meat - beef - brisket',
 'meat - beef - chuck roast',
 'meat - beef - ribs',
 'meat - beef - steak',
 'meat - fish',
 'meat - fish - mahi mahi',
 'meat - fish - salmon',
 'meat - fish - shellfish - clams',
 'meat - fish - shellfish - lobster',
 'meat - fish - shellfish - mussel',
 'meat - fish - shellfish - scallops',
 'meat - fish - shellfish - shrimp',
 'meat - fish - tuna',
 'meat - other meat - bison',
 'meat - other meat - lamb',
 'meat - pork - bacon',
 'meat - pork - ham',
 'meat - pork - pancetta',
 'meat - pork - pork',
 'meat - pork - pork chop',
 'meat - poultry - chicken',
 'meat - poultry - turkey',
 'meat - processed meat - deli meat',
 'meat - processed meat - prosciutto',
 'meat - 

### alternatives to non-vegan ingredients

In [13]:
df_non_vegan_alter = pd.read_csv('nonvegan-alternatives.csv')
df_non_vegan_alter


BaseIngredient       VeganAlternative
0             anchovy             miso paste
1           bbq sauce           Hoisin sauce
2                beer        sparkling water
3       buffalo sauce              hot sauce
4              butter            coconut oil
..                ...                    ...
56   pickled jalapeño  jalapeño with vinegar
57  poultry seasoning                  herbs
58          rice wine           Rice vinegar
59             sherry             white wine
60            tequila             Lime juice

[61 rows x 2 columns]

## Function - Mapping Non-Vegan ingredient to Vegan Ing.

In [14]:
def conver_to_vegan(ingr_list):
    vegan_list = []
    for i in ingr_list:
        if i in non_vegan_ingr:
            filtered_df = df_non_vegan_alter[df_non_vegan_alter['BaseIngredient'] == i]
            # Get the comma-separated strings from column 'VeganAlternative'
            vegan_alternatives = filtered_df['VeganAlternative']
            # Split the strings by comma and flatten the list
            result_list = [item.strip() for sublist in vegan_alternatives.str.split(',') for item in sublist]
            for alter in result_list:
                vegan_list.append(alter)
        else:
            vegan_list.append(i)
            
    return vegan_list

In [15]:
df['vegan_ingredients'] = df['base_ingredients'].apply(conver_to_vegan)

In [16]:
df

title          prep_time  \
0        25 Minute Ginger Steak Mango Cucumber Bowls  {'minutes': '15'}   
1                         The Italian Salad Sandwich  {'minutes': '25'}   
2                Grilled Buffalo Ranch Chicken Tacos  {'minutes': '20'}   
3     Chicken Quesadillas with Creamy Chipotle Sauce  {'minutes': '20'}   
4      Sesame Ginger Steak Skewers with Peanut Sauce  {'minutes': '15'}   
...                                              ...                ...   
2345                         Fig Bourbon Cider Smash   {'minutes': '5'}   
2346                        Salted Watermelon Paloma  {'minutes': '10'}   
2347                      Blackberry Thyme Margarita   {'minutes': '5'}   
2348                    Sweet Bourbon Peach Lemonade   {'minutes': '5'}   
2349                    Hibiscus Cherry Vodka Spritz  {'minutes': '15'}   

              cook_time         total_time  \
0     {'minutes': '10'}  {'minutes': '25'}   
1      {'minutes': '5'}  {'minutes': '30'}   
2     {'minutes': '20'}  {'minutes': '40'}   
3     {'minutes': '10'}  {'minutes': '30'}   
4     {'minutes': '15'}  {'minutes': '30'}   
...                 ...                ...   
2345                  -   {'minutes': '5'}   
2346                  -  {'minutes': '10'}   
2347                  -   {'minutes': '5'}   
2348                  -   {'minutes': '5'}   
2349   {'minutes': '5'}  {'minutes': '20'}   

                                            ingredients  \
0     [lime juice, toasted sesame oil, fish sauce, f...   
1     [extra virgin olive oil, champagne vinegar, fi...   
2     [boneless chicken tenders or small thighs, sea...   
3     [canned chipotle chiles in adobo, extra virgin...   
4     [creamy peanut butter, tamari/soy sauce, Thai ...   
...                                                 ...   
2345  [apple cider, orange zest + 2 tablespoons juic...   
2346  [cubed watermelon, kosher salt, Florida’s Natu...   
2347  [fresh blackberries, small red plum, quartered...   
2348  [Florida's Natural® Brand Lemonade with Raspbe...   
2349  [fresh cherries, dried hibiscus flowers, honey...   

                           ingredients with measurement  \
0     {'lime juice': '2', 'toasted sesame oil': '3',...   
1     {'extra virgin olive oil': '1/2', 'champagne v...   
2     {'boneless chicken tenders or small thighs': '...   
3     {'canned chipotle chiles in adobo': '1/2', 'ex...   
4     {'creamy peanut butter': '1/2', 'tamari/soy sa...   
...                                                 ...   
2345  {'apple cider': '1/4', 'orange zest + 2 tables...   
2346  {'cubed watermelon': '2', 'kosher salt': 'seas...   
2347  {'fresh blackberries': '8', 'small red plum, q...   
2348  {"Florida's Natural® Brand Lemonade with Raspb...   
2349  {'fresh cherries': '3/4', 'dried hibiscus flow...   

                                           instructions  calories  servings  \
0     ['1. To make the dressing. Combine all ingredi...  472 kcal         6   
1     ['1. To make the dressing. Combine all ingredi...  699 kcal         6   
2     ['1. Set your grill, grill pan, or skillet to ...  582 kcal         6   
3     ["1. To make the dressing. Combine all ingredi...  672 kcal         4   
4     ['1. To make the peanut sauce. Add all ingredi...  419 kcal         6   
...                                                 ...       ...       ...   
2345  ['1. In a cocktail shaker, combine the apple c...   52 kcal         1   
2346  ['1. Add the watermelon to a blender and pulse...   68 kcal         1   
2347  ['1.\xa0Run a lime wedge around the rim of you...   84 kcal         1   
2348  ['1. In a blender, combine the lemonade and pe...  136 kcal         8   
2349  ['1. Add the cherries to a medium size pot. Us...  158 kcal         4   

                                                 images type_of_meal  \
0     https://www.halfbakedharvest.com/wp-content/up...  main-course   
1     https://www.halfbakedharvest.com/wp-content/up...  main-course   
2     http

In [17]:
# user_ingrs = ['lime', 'sesame oil','garlic', 'fish sauce', 'ginger','bell pepper','tofu','cashew cheese','honey','butter','chili paste']

In [18]:
user_ingrs = ['sugar', 'brown sugar','vanilla extract','honey','cream cheese','butter','baking soda','chocolate chips']

## Function - Creating Tags with Available Vegan Ingr.

In [19]:
def vegan_with_available(ingr_list,user_ingrs):
    vegan_list = []
    for i in ingr_list:
        if i in non_vegan_ingr:
            filtered_df = df_non_vegan_alter[df_non_vegan_alter['BaseIngredient'] == i]
            vegan_alternatives = filtered_df['VeganAlternative']
            result_list = [item.strip() for sublist in vegan_alternatives.str.split(',') for item in sublist]
            
            found = False
            for alter in result_list:
                if alter in user_ingrs:
                    vegan_list.append(alter)
                    found = True
                    break
            if not found:
                vegan_list.append(result_list[0])
        else:
            vegan_list.append(i)
    result_string = ', '.join(vegan_list)
    return str(result_string)


df['tags'] = df['base_ingredients'].apply(lambda x: vegan_with_available(x, user_ingrs))

## Function - Mapping Non-Vegan ingredient to Available Vegan Ing. in INSTRUCTIONS

In [20]:
def instructions_with_vegan_available(instructions, ingr_list):
    print(instructions)
    for i in ingr_list:
        if i in non_vegan_ingr:
            filtered_df = df_non_vegan_alter[df_non_vegan_alter['BaseIngredient'] == i]
            vegan_alternatives = filtered_df['VeganAlternative']
            result_list = [item.strip() for sublist in vegan_alternatives.str.split(',') for item in sublist]
            found = False
            for alter in result_list:
                if alter in user_ingrs:
                    instructions = instructions.replace(i, alter)
                    found = True
                    break
            if not found:
                instructions = instructions.replace(i, result_list[0])
    return instructions       
df['instructions'] = df.apply(lambda row: instructions_with_vegan_available(row['instructions'], row['base_ingredients']), axis=1)


['1. To make the dressing. Combine all ingredients in a jar. Season to taste with chili flakes.', '2. In a bowl, toss the steak with tamari and 2-3 tablespoons of the dressing, rubbing the dressing onto the steak.', '3. Set your grill, grill pan, or skillet to medium-high heat. Grill the steak until lightly charred, 5-8 minutes for medium-rare, per side. Remove the steaks and allow them to rest for 5-10 minutes. Slice the steak.', '4. Meanwhile, in a bowl, toss the cucumbers with pickled ginger and 3 tablespoons dressing. In a separate bowl, toss the mango with herbs, lime juice, and chili flakes.', '5. Spoon the reserved dressing over the slices of steak, then serve the steak over bowls of rice. Top with cucumber, mango, avocado, and peanuts. Enjoy!']
['1. To make the dressing. Combine all ingredients in a glass jar and whisk until smooth. Taste and adjust the salt and chili flakes', '2. Preheat the grill or grill pan to high.\xa0Rub each half of the bread with some dressing. Grill th

In [21]:
df

title          prep_time  \
0        25 Minute Ginger Steak Mango Cucumber Bowls  {'minutes': '15'}   
1                         The Italian Salad Sandwich  {'minutes': '25'}   
2                Grilled Buffalo Ranch Chicken Tacos  {'minutes': '20'}   
3     Chicken Quesadillas with Creamy Chipotle Sauce  {'minutes': '20'}   
4      Sesame Ginger Steak Skewers with Peanut Sauce  {'minutes': '15'}   
...                                              ...                ...   
2345                         Fig Bourbon Cider Smash   {'minutes': '5'}   
2346                        Salted Watermelon Paloma  {'minutes': '10'}   
2347                      Blackberry Thyme Margarita   {'minutes': '5'}   
2348                    Sweet Bourbon Peach Lemonade   {'minutes': '5'}   
2349                    Hibiscus Cherry Vodka Spritz  {'minutes': '15'}   

              cook_time         total_time  \
0     {'minutes': '10'}  {'minutes': '25'}   
1      {'minutes': '5'}  {'minutes': '30'}   
2     {'minutes': '20'}  {'minutes': '40'}   
3     {'minutes': '10'}  {'minutes': '30'}   
4     {'minutes': '15'}  {'minutes': '30'}   
...                 ...                ...   
2345                  -   {'minutes': '5'}   
2346                  -  {'minutes': '10'}   
2347                  -   {'minutes': '5'}   
2348                  -   {'minutes': '5'}   
2349   {'minutes': '5'}  {'minutes': '20'}   

                                            ingredients  \
0     [lime juice, toasted sesame oil, fish sauce, f...   
1     [extra virgin olive oil, champagne vinegar, fi...   
2     [boneless chicken tenders or small thighs, sea...   
3     [canned chipotle chiles in adobo, extra virgin...   
4     [creamy peanut butter, tamari/soy sauce, Thai ...   
...                                                 ...   
2345  [apple cider, orange zest + 2 tablespoons juic...   
2346  [cubed watermelon, kosher salt, Florida’s Natu...   
2347  [fresh blackberries, small red plum, quartered...   
2348  [Florida's Natural® Brand Lemonade with Raspbe...   
2349  [fresh cherries, dried hibiscus flowers, honey...   

                           ingredients with measurement  \
0     {'lime juice': '2', 'toasted sesame oil': '3',...   
1     {'extra virgin olive oil': '1/2', 'champagne v...   
2     {'boneless chicken tenders or small thighs': '...   
3     {'canned chipotle chiles in adobo': '1/2', 'ex...   
4     {'creamy peanut butter': '1/2', 'tamari/soy sa...   
...                                                 ...   
2345  {'apple cider': '1/4', 'orange zest + 2 tables...   
2346  {'cubed watermelon': '2', 'kosher salt': 'seas...   
2347  {'fresh blackberries': '8', 'small red plum, q...   
2348  {"Florida's Natural® Brand Lemonade with Raspb...   
2349  {'fresh cherries': '3/4', 'dried hibiscus flow...   

                                           instructions  calories  servings  \
0     ['1. To make the dressing. Combine all ingredi...  472 kcal         6   
1     ['1. To make the dressing. Combine all ingredi...  699 kcal         6   
2     ['1. Set your grill, grill pan, or skillet to ...  582 kcal         6   
3     ["1. To make the dressing. Combine all ingredi...  672 kcal         4   
4     ['1. To make the peanut sauce. Add all ingredi...  419 kcal         6   
...                                                 ...       ...       ...   
2345  ['1. In a cocktail shaker, combine the apple c...   52 kcal         1   
2346  ['1. Add the watermelon to a blender and pulse...   68 kcal         1   
2347  ['1.\xa0Run a lime wedge around the rim of you...   84 kcal         1   
2348  ['1. In a blender, combine the lemonade and pe...  136 kcal         8   
2349  ['1. Add the cherries to a medium size pot. Us...  158 kcal         4   

                                                 images type_of_meal  \
0     https://www.halfbakedharvest.com/wp-content/up...  main-course   
1     https://www.halfbakedharvest.com/wp-content/up...  main-course   
2     http

## Function - Recipes with atleast 3 ingredients available

In [22]:
# Function to check if the user has at least 3 ingredients for a recipe
def check_ingredients(recipe_ingredients, user_ingredients):
#     print(recipe_ingredients)
    recipe_ingredients_set = set(recipe_ingredients)
    common_ingredients = recipe_ingredients_set.intersection(user_ingredients)
    return len(common_ingredients) >= 3

# Apply the function to each recipe
df['HasEnoughIngredients'] = df['vegan_ingredients'].apply(lambda x: check_ingredients(x, user_ingrs))

# Filter the recipes
suitable_recipes = df[df['HasEnoughIngredients']]

print("Recipes with at least 3 matching ingredients:")
suitable_recipes

Recipes with at least 3 matching ingredients:


title          prep_time  \
1110                  Frosted Brown Sugar Pop Tart Bars  {'minutes': '30'}   
1111                            Caramel Peach Dump Cake  {'minutes': '15'}   
1112              Chocolate Chip Sour Cream Coffee Cake  {'minutes': '25'}   
1113  Banana Bread Carrot Cake with Vanilla Cream Ch...  {'minutes': '20'}   
1114       Salted Butter Coconut Chocolate Chip Cookies  {'minutes': '15'}   
...                                                 ...                ...   
1783  Apple Pecan Pie Cronuts with Apple Cider Caram...  {'minutes': '20'}   
1789  Fudge Brownie, Caramel, Popcorn + Oatmeal Cook...  {'minutes': '15'}   
1790  Cinnamon Swirl Chocolate Chip Pumpkin Butter B...  {'minutes': '20'}   
1791  Brown Butter Apple Blondies with Cinnamon Mapl...  {'minutes': '15'}   
1794  Giant S'mores Stuffed Chocolate Chip Skillet C...  {'minutes': '15'}   

              cook_time                       total_time  \
1110  {'minutes': '45'}  {'hours': '1', 'minutes': '15'}   
1111     {'hours': '1'}  {'hours': '1', 'minutes': '15'}   
1112     {'hours': '1'}  {'hours': '1', 'minutes': '25'}   
1113     {'hours': '1'}  {'hours': '1', 'minutes': '20'}   
1114  {'minutes': '15'}                {'minutes': '30'}   
...                 ...                              ...   
1783  {'minutes': '40'}                   {'hours': '2'}   
1789  {'minutes': '45'}   {'hours': '3', 'minutes': '5'}   
1790  {'minutes': '50'}  {'hours': '1', 'minutes': '10'}   
1791  {'minutes': '25'}                {'minutes': '45'}   
1794  {'minutes': '25'}                {'minutes': '40'}   

                                            ingredients  \
1110  [all-purpose flour, dark brown sugar, cold sal...   
1111  [peaches, quartered, salted butter, cubed, bro...   
1112  [all-purpose or whole wheat pastry flour, baki...   
1113  [medium overly ripe bananas, mashed, grated ca...   
1114  [salted butter, at room temperature, brown sug...   
...                                                 ...   
1783  [of this [croissant dough | http://go.foodgawk...   
1789  [canola oil, butter, cocoa powder, eggs, sugar...   
1790  [pumpkin butter, pumpkin puree, melted salted ...   
1791  [salted butter, apple butter, light brown suga...   
1794  [salted butter, at room temperature, dark brow...   

                           ingredients with measurement  \
1110  {'all-purpose flour': '1', 'dark brown sugar':...   
1111  {'peaches, quartered': '8', 'salted butter, cu...   
1112  {'all-purpose or whole wheat pastry flour': '1...   
1113  {'medium overly ripe bananas, mashed': '3', 'g...   
1114  {'salted butter, at room temperature': '2', 'b...   
...                                                 ...   
1783  {'of this [croissant dough | http://go.foodgaw...   
1789  {'canola oil': '1/3', 'butter': '4', 'cocoa po...   
1790  {'pumpkin butter': '1/2', 'pumpkin puree': '1/...   
1791  {'salted butter': '3', 'apple butter': '1/2', ...   
1794  {'salted butter, at room temperature': '2', 'd...   

                                           instructions   calories  servings  \
1110  ['1. To make the cookie dough. In a bowl using...   291 kcal        16   
1111  ['1. Preheat the oven to 375° F.', '2. Arrange...   392 kcal         8   
1112  ['1. Preheat the oven to 350° F. Line a (9×9 i...   291 kcal        15   
1113  ['1. Preheat the oven to 350° F. Grease a 9×5 ...   436 kcal         8   
1114  ['1. Preheat the oven to 350° F. Line a baking...   312 kcal        18   
...                                                 ...        ...       ...   
1783                                                 []   451 kcal         8   
1789                                                 []   397 kcal        20   
1790  ['1. Preheat the oven to 350° F. Grease a (9x5...  2873 kcal         1   
1791  ['1. Preheat the oven to 350 degrees F.\xa0Lin...   218 kcal        24   
1794  ['1. Preheat the oven to 350 degrees F. Lightl...   483 kcal        12   

             

In [23]:
from sklearn.feature_extraction.text import CountVectorizer

# Initialize CountVectorizer to create a binary matrix of ingredients
vectorizer = CountVectorizer(tokenizer=lambda x: x.split(', '))
X = vectorizer.fit_transform(suitable_recipes['tags'])

# Convert to DataFrame
ingredient_df = pd.DataFrame(X.toarray(), columns=vectorizer.get_feature_names_out())

print("Ingredient Matrix:")
print(ingredient_df)


Ingredient Matrix:
     agar-agar  all purpose flour  almond  almond milk  apple  \
0            0                  1       0            0      0   
1            0                  1       0            1      0   
2            0                  1       0            0      0   
3            0                  0       0            0      0   
4            0                  1       0            0      0   
..         ...                ...     ...          ...    ...   
292          0                  0       0            1      0   
293          0                  1       0            1      0   
294          0                  1       0            0      0   
295          0                  1       0            0      0   
296          0                  1       0            0      0   

     apple cider vinegar  avocado  baking powder  baking soda  banana  ...  \
0                      0        0              0            0       0  ...   
1                      0        0           

In [25]:
from sklearn.metrics.pairwise import cosine_similarity


# user_ingrs
# Convert user ingredients into a feature vector
user_vector = vectorizer.transform([', '.join(user_ingrs)])

# Compute cosine similarity between user ingredients and recipes
similarities = cosine_similarity(user_vector, X).flatten()

# Add similarity scores to the DataFrame
suitable_recipes['Similarity'] = similarities

# Recommend recipes with the highest similarity scores
recommended_recipes = suitable_recipes.sort_values(by='Similarity', ascending=False)


print("Recommended Recipes:")
print(recommended_recipes[['title', 'Similarity']])


Recommended Recipes:
                                                  title  Similarity
1430  The Best Chocolate Chip Peanut Butter Swirled ...    0.666667
1289          Crème Fraîche Chocolate Chunk Cookie Bars    0.666667
1712      Brown Butter Raspberry Chocolate Chip Cookies    0.632456
1449    The Best Oatmeal Chocolate Chip Cookies Around.    0.632456
1114       Salted Butter Coconut Chocolate Chip Cookies    0.632456
...                                                 ...         ...
1189                    Sugar Cookie Hot Cocoa Cupcakes    0.319801
1646                            Gingerbread Man Granola    0.312772
1738                Salted Caramel Apple Snickers Cake.    0.312772
1402  (The Cheaters Way) Deathly Chocolate Graveyard...    0.294174
1230                                 Fudge Brownie Mix.    0.246598

[297 rows x 2 columns]


/var/folders/vx/738z10qd2gb7rhy7_rz19c3w0000gn/T/ipykernel_6307/28331436.py:12: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  suitable_recipes['Similarity'] = similarities


In [27]:
recommended_recipes['instructions'].loc[1712]

"['1. Preheat the oven to 350° F. Line a baking sheet with parchment paper.', '2. Add the coconut oil to a skillet set over medium heat. Cook until the coconut oil begins to brown, about 3-4 minutes. Remove from the heat and transfer to a heatproof bowl. Let cool 5 minutes or so.', '3. To the brown coconut oil, mix in the brown sugar, granulated sugar, Silken tofus, and vanilla, mixing until smooth. Add the flour, baking soda, and salt. Gently fold in the cocoa powder and raspberries, do not overmix.', '4. Roll the dough into rounded tablespoon size balls and place 2 inches apart on the prepared baking sheet. The dough may be a little wet from the berries. Gently flatten the dough down. Bake 8 minutes. Remove from the oven, rotate and tap the baking sheet on the counter 1-2 times to flatten. Bake another 2-3 minutes or until the cookies are just beginning to set on the edges.', '5. Let the cookies cool on the baking sheet. They will continue to cook slightly as they sit on the baking s

In [28]:
recommended_recipes

title          prep_time  \
1430  The Best Chocolate Chip Peanut Butter Swirled ...  {'minutes': '15'}   
1289          Crème Fraîche Chocolate Chunk Cookie Bars  {'minutes': '20'}   
1712      Brown Butter Raspberry Chocolate Chip Cookies  {'minutes': '15'}   
1449    The Best Oatmeal Chocolate Chip Cookies Around.  {'minutes': '10'}   
1114       Salted Butter Coconut Chocolate Chip Cookies  {'minutes': '15'}   
...                                                 ...                ...   
1189                    Sugar Cookie Hot Cocoa Cupcakes  {'minutes': '30'}   
1646                            Gingerbread Man Granola  {'minutes': '25'}   
1738                Salted Caramel Apple Snickers Cake.     {'hours': '1'}   
1402  (The Cheaters Way) Deathly Chocolate Graveyard...  {'minutes': '30'}   
1230                                 Fudge Brownie Mix.  {'minutes': '10'}   

              cook_time                       total_time  \
1430  {'minutes': '25'}                {'minutes': '40'}   
1289  {'minutes': '30'}                {'minutes': '50'}   
1712  {'minutes': '15'}                {'minutes': '30'}   
1449  {'minutes': '10'}                {'minutes': '20'}   
1114  {'minutes': '15'}                {'minutes': '30'}   
...                 ...                              ...   
1189  {'minutes': '25'}                   {'hours': '1'}   
1646  {'minutes': '40'}  {'hours': '2', 'minutes': '10'}   
1738  {'minutes': '45'}                   {'hours': '4'}   
1402  {'minutes': '20'}                {'minutes': '50'}   
1230  {'minutes': '50'}                   {'hours': '3'}   

                                            ingredients  \
1430  [salted butter, at room temperature, light bro...   
1289  [salted butter, at room temperature, light bro...   
1712  [salted butter at room temperature, brown suga...   
1449  [old fashioned oats, all-purpose flour, granul...   
1114  [salted butter, at room temperature, brown sug...   
...                                                 ...   
1189  [unsalted butter, granulated sugar, vanilla ex...   
1646  [flour, white whole wheat flour or whole wheat...   
1738  [all-purpose flour, granulated sugar, unsweete...   
1402  [box chocolate cake mix, Kahlua OR caramel sau...   
1230  [glass jar, Bob's Red Mill All-Purpose Flour, ...   

                           ingredients with measurement  \
1430  {'salted butter, at room temperature': '2', 'l...   
1289  {'salted butter, at room temperature': '2', 'l...   
1712  {'salted butter at room temperature': '2', 'br...   
1449  {'old fashioned oats': '2 1/2', 'all-purpose f...   
1114  {'salted butter, at room temperature': '2', 'b...   
...                                                 ...   
1189  {'unsalted butter': '7', 'granulated sugar': '...   
1646  {'flour': '3/4', 'white whole wheat flour or w...   
1738  {'all-purpose flour': '2 1/4', 'granulated sug...   
1402  {'box chocolate cake mix': '1', 'Kahlua OR car...   
1230  {'glass jar': '1', "Bob's Red Mill All-Purpose...   

                                           instructions   calories  servings  \
1430  ['1. Preheat the oven to 350 degrees F. Grease...  1527 kcal        24   
1289  ['1. Preheat the oven to 350 degrees F. Grease...  1616 kcal        24   
1712  ['1. Preheat the oven to 350° F. Line a baking...   203 kcal        24   
1449                                                 []   260 kcal        27   
1114  ['1. Preheat the oven to 350° F. Line a baking...   312 kcal        18   
...                                                 ...        ...       ...   
1189                                                 []   823 kcal        12   
1646                                                 []  1165 kcal         6   
1738  ['In the bowl of a stand mixer (or use a hand ...   953 kcal        16   
1402                                                 []  1009 kcal         6   
1230                                                 []   221 kcal        24   

             